In [ ]:
# Learning Practice 8 for the University of Tulsa's QM-7063 Data Mining Course
# K-Nearest Neighbor and Naive Bayes
# Professor: Dr. Abdulrashid, Spring 2023
# Noah L. Schrick - 1492657

In [16]:
# Imports

%matplotlib inline

from pathlib import Path

import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import mean_squared_error
from math import sqrt

import matplotlib.pylab as plt
from dmba import classificationSummary, gainsChart

from sklearn import preprocessing
from sklearn.metrics import accuracy_score
from sklearn.neighbors import NearestNeighbors, KNeighborsClassifier, KNeighborsRegressor

# Problem 7.3 Predicting Housing Median Prices
The file BostonHousing.csv contains information on over 500 census tracts in Boston, where for each tract multiple variables are recorded. The last column (CAT.MEDV) was derived from MEDV, such that it obtains the value 1 if MEDV > 30 and 0 otherwise. Consider the goal of predicting
the median value (MEDV) of a tract, given the information in the first 12 columns. 

Partition the data into training (60%) and validation (40%) sets.

In [64]:
# Pre-processing
housing_df = pd.read_csv('BostonHousing.csv')
trainData, validData = train_test_split(housing_df, test_size=0.4, random_state=26)

# a. 
Perform a k-NN prediction with all 12 predictors (ignore the CAT.MEDV column), trying values of k from 1 to 5. Make sure to normalize the data. What is the best k? What does it mean?

In [68]:
# a
## Normalize
scaler = preprocessing.StandardScaler()

predictors = housing_df.columns.values.tolist()
predictors.remove('CAT. MEDV')
predictors.remove('MEDV')

scaler.fit(trainData[predictors])  # Note the use of an array of column names

# Transform the full dataset
housingNorm = pd.concat([pd.DataFrame(scaler.transform(housing_df[predictors]), 
                                    columns=predictors),
                        housing_df[['MEDV']]], axis=1)

trainNorm = housingNorm.iloc[trainData.index]
validNorm = housingNorm.iloc[validData.index]
#newHousingNorm = pd.DataFrame(scaler.transform(housingNorm), columns=predictors)

In [69]:
## K-NN
results = []
train_X = trainNorm[predictors]
train_y = trainNorm['MEDV']
valid_X = validNorm[predictors]
valid_y = validNorm['MEDV']

for k in range(1,5):
    knn = KNeighborsRegressor(n_neighbors=k).fit(train_X, train_y)
    results.append({
        'k': k,
        'accuracy': knn.score(valid_X, valid_y)
    })

# Convert results to a pandas data frame
results = pd.DataFrame(results)
print(results)

   k  accuracy
0  1  0.643141
1  2  0.720241
2  3  0.710570
3  4  0.676896


The best k is k=2. This means we have greater accuracy when each point has its nearest 2 neighbors identified.

# b. 
Predict the MEDV for a tract with the following information, using the best k:
CRIM    ZN    INDUS    CHAS    NOX    RM    AGE    DIS    RAD    TAX    PTRATIO    LSTAT
 0.2     0      7        0    0.538    6     62    4.7      4    307      21         10


In [73]:
# b
sample = [[0.2, 0, 7, 0, 0.538, 6, 62, 4.7, 4, 307, 21, 10]]
sample_norm = scaler.transform(sample)
ans_b = knn.predict(sample_norm)
print(ans_b)

[19.45]


/home/noah/.local/lib/python3.10/site-packages/sklearn/base.py:420: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/home/noah/.local/lib/python3.10/site-packages/sklearn/base.py:420: UserWarning: X does not have valid feature names, but KNeighborsRegressor was fitted with feature names
  warnings.warn(


# c. 
If we used the above k-NN algorithm to score the training data, what would be the error of the training set?

Error will be zero, or close to zero. Since the training data was used to build the model, checking the training data against itself should yield very high accuracy.

# d. 
Why is the validation data error overly optimistic compared to the error rate when applying this k-NN predictor to new data?

# d.
This model was built and tuned with a specific k value (k=2). This value of k was the best for the data used, but does not mean that this value of k is the best for future data.

# e. 
If the purpose is to predict MEDV for several thousands of new tracts, what would be the disadvantage of using k-NN prediction? List the operations that the algorithm goes through in order to produce each prediction.

# e.

1. Select k-nearest samples
2. Compute average value for k-nearest neighbors
3. Score value with new data
4. Repeat for all new data samples

If there are several thousands of new tracts, then k-NN will take much longer to run. The model will need to be rebuilt numerous times over the several thousand pieces of data. The lack of scalability will be a disadvantage. 

# Problem 8.2 Automobile Accidents
The file accidentsFull.csv contains information on 42,183 actual automobile accidents in 2001 in the United States that involved one of three levels of injury: NO INJURY, INJURY, or FATALITY. For each accident, additional information is recorded, such as day of week, weather conditions, and road type. A firm might be interested in developing a system for quickly classifying the severity of an accident based on initial reports and associated data in the system (some of which rely on GPS-assisted reporting).

Our goal here is to predict whether an accident just reported will involve an injury (MAX_SEV_IR = 1 or 2) or will not (MAX_SEV_IR = 0). For this purpose, create a dummy variable called INJURY that takes the value “yes” if MAX_SEV_IR = 1 or 2, and otherwise "no".

# a. 
Using the information in this dataset, if an accident has just been reported and no further information is available, what should the prediction be? (INJURY = Yes or No?) Why?


# b. 
Select the first 12 records in the dataset and look only at the response (INJURY) and the two predictors WEATHER_R and TRAF_CON_R.


In [ ]:
# b.

# i. 
Create a pivot table that examines INJURY as a function of the two predictors for these 12 records. Use all three variables in the pivot table as rows/columns.


In [ ]:
# i.

# ii. 
Compute the exact Bayes conditional probabilities of an injury (INJURY = Yes) given the six possible combinations of the predictors.


In [ ]:
# ii.

# iii. 
Classify the 12 accidents using these probabilities and a cutoff of 0.5.


In [ ]:
# iii.

# iv. 
Compute manually the naive Bayes conditional probability of an injury given WEATHER_R = 1 and TRAF_CON_R = 1.


In [ ]:
# iv.

# v.
Run a naive Bayes classifier on the 12 records and 2 predictors using scikit-
learn. Check the model output to obtain probabilities and classifications for all
12 records. Compare this to the exact Bayes classification. Are the resulting
classifications equivalent? Is the ranking (=ordering) of observations equiva-
lent?


In [ ]:
# v.

# c. 
Let us now return to the entire dataset. Partition the data into training (60%) and validation (40%).


In [ ]:
# c.

# i. 
Assuming that no information or initial reports about the accident itself are available at the time of prediction (only location characteristics, weather conditions, etc.), which predictors can we include in the analysis? (Use the data descriptions page from www.dataminingbook.com.)


In [ ]:
# i

# ii. 
Run a naive Bayes classifier on the complete training set with the relevant predictors (and INJURY as the response). Note that all predictors are categorical. Show the confusion matrix.


In [ ]:
# ii.

# iii. 
What is the overall error for the validation set?


In [ ]:
# iii.

# iv. 
What is the percent improvement relative to the naive rule (using the validation set)?


In [ ]:
# iv.

# v. 
Examine the conditional probabilities in the pivot tables. Why do we get a probability of zero for P(INJURY = No j SPD_LIM = 5)?

In [ ]:
# v.